In [ ]:
#from google.colab import drive
#drive.mount('/content/drive/')
# write the directory that has all the files
Directory = '/content/drive/MyDrive/ECML2024-SSTA/'

Mounted at /content/drive/


In [ ]:
#import torch
#
#!pip uninstall torch-scatter torch-sparse torch-geometric torch-cluster  --y
#!pip install torch-scatter -f https://data.pyg.org/whl/torch-{torch.__version__}.html
#!pip install torch-sparse -f https://data.pyg.org/whl/torch-{torch.__version__}.html
#!pip install torch-cluster -f https://data.pyg.org/whl/torch-{torch.__version__}.html
#!pip install git+https://github.com/pyg-team/pytorch_geometric.git
#!pip install graph-weather

In [ ]:
!pip install catboost

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 98.2/98.2 MB 21.3 MB/s eta 0:00:00


In [ ]:
import pandas as pd
import numpy as np
#from kan import *
from sklearn.model_selection import StratifiedKFold,KFold
from catboost import CatBoostRegressor
from sklearn.metrics import mean_squared_error
from sklearn.neighbors import KNeighborsRegressor
import xgboost
import lightgbm
from sklearn.ensemble import RandomForestRegressor
from sklearn import linear_model

In [ ]:
locations = num_nodes = 5774

In [ ]:
coords = pd.read_csv(f'{Directory}coords.csv',header=None)
test_mlsp = pd.read_csv(f'{Directory}test_input_mslp_phase_two.csv',header=None).to_numpy()
test_sst = pd.read_csv(f'{Directory}test_input_sst_phase_two.csv',header=None).to_numpy()
test_ssta = pd.read_csv(f'{Directory}test_input_ssta_phase_two.csv',header=None).to_numpy()
test_t2m = pd.read_csv(f'{Directory}test_input_t2m_phase_two.csv',header=None).to_numpy()
val_mlsp = pd.read_csv(f'{Directory}test_input_mslp_phase_one.csv',header=None).to_numpy()
val_sst = pd.read_csv(f'{Directory}test_input_sst_phase_one.csv',header=None).to_numpy()
val_ssta = pd.read_csv(f'{Directory}test_input_ssta_phase_one.csv',header=None).to_numpy()
val_t2m = pd.read_csv(f'{Directory}test_input_t2m_phase_one.csv',header=None).to_numpy()

train_mlsp = pd.read_csv(f'{Directory}training_input_mslp.csv',header=None).to_numpy()
train_sst = pd.read_csv(f'{Directory}training_input_sst.csv',header=None).to_numpy()
train_ssta = pd.read_csv(f'{Directory}training_input_ssta.csv',header=None).to_numpy()
train_t2m = pd.read_csv(f'{Directory}training_input_t2m.csv',header=None).to_numpy()
train_out = pd.read_csv(f'{Directory}training_output.csv',header=None).to_numpy()

In [ ]:
prep_val_mlsp = np.zeros((639,5774))
prep_val_sst = np.zeros((639,5774))
prep_val_ssta = np.zeros((639,5774))
prep_val_t2m = np.zeros((639,5774))
prep_val_out = np.zeros((639,5774))
prep_test_mlsp = np.zeros((639,5774))
prep_test_sst = np.zeros((639,5774))
prep_test_ssta = np.zeros((639,5774))
prep_test_t2m = np.zeros((639,5774))
prep_test_out = np.zeros((639,5774))
selected_indices = list(range(11, len(test_ssta), 12))
for i in range(len(selected_indices)):
  prep_test_mlsp[9*i:(9*(i+1)),:] = test_mlsp[selected_indices[i]-11:selected_indices[i]-2,:]
  prep_test_sst[9*i:(9*(i+1)),:] = test_sst[selected_indices[i]-11:selected_indices[i]-2,:]
  prep_test_ssta[9*i:(9*(i+1)),:] = test_ssta[selected_indices[i]-11:selected_indices[i]-2,:]
  prep_test_t2m[9*i:(9*(i+1)),:] = test_t2m[selected_indices[i]-11:selected_indices[i]-2,:]
  prep_test_out[9*i:(9*(i+1)),:] = test_ssta[selected_indices[i]-8:selected_indices[i]+1,:]
  prep_val_mlsp[9*i:(9*(i+1)),:] = val_mlsp[selected_indices[i]-11:selected_indices[i]-2,:]
  prep_val_sst[9*i:(9*(i+1)),:] = val_sst[selected_indices[i]-11:selected_indices[i]-2,:]
  prep_val_ssta[9*i:(9*(i+1)),:] = val_ssta[selected_indices[i]-11:selected_indices[i]-2,:]
  prep_val_t2m[9*i:(9*(i+1)),:] = val_t2m[selected_indices[i]-11:selected_indices[i]-2,:]
  prep_val_out[9*i:(9*(i+1)),:] = val_ssta[selected_indices[i]-8:selected_indices[i]+1,:]

In [ ]:
train_mean_ssta = np.zeros_like(train_ssta)
train_mean_sst = np.zeros_like(train_ssta)
train_std_ssta = np.zeros_like(train_ssta)
train_std_sst = np.zeros_like(train_ssta)
for i in range(train_ssta.shape[0]):
  train_mean_ssta[i,:] =  np.mean(train_ssta[max(0,i-11):i+1,:]) - train_ssta[i,:]
  train_mean_sst[i,:] =  np.mean(train_sst[max(0,i-11):i+1,:]) - train_sst[i,:]
  train_std_ssta[i,:] =  np.std(train_ssta[max(0,i-11):i+1,:])
  train_std_sst[i,:] =  np.std(train_sst[max(0,i-11):i+1,:])



In [ ]:
test_predictions = np.zeros((71, 5774))
for l in range(locations):
  print(l)
  index = l
  train_len = train_ssta.shape[0]+prep_val_ssta.shape[0]
  val_len = prep_val_ssta.shape[0]
  input = np.zeros((train_len,4))
  output = np.zeros((train_len,1))
  val_input = np.zeros((val_len,4))
  val_output = np.zeros((val_len,1))

  input[:,0] = np.concatenate((train_mlsp[:,index], prep_val_mlsp[:,index]))
  input[:,1] = np.concatenate((train_sst[:,index], prep_val_sst[:,index]))
  input[:,2] = np.concatenate((train_t2m[:,index], prep_val_t2m[:,index]))
  input[:,3] = np.concatenate((train_ssta[:,index], prep_val_ssta[:,index]))
  output[:,0] = np.concatenate((train_out[:,index], prep_val_out[:,index]))

  val_input[:,0] = prep_test_mlsp[:,index]
  val_input[:,1] = prep_test_sst[:,index]
  val_input[:,2] = prep_test_t2m[:,index]
  val_input[:,3] = prep_test_ssta[:,index]
  val_output[:,0] = prep_test_out[:,index]

  test_input = np.zeros((len(selected_indices),4))
  test_input[:,0] = test_mlsp[selected_indices,index]
  test_input[:,1] = test_sst[selected_indices,index]
  test_input[:,2] = test_t2m[selected_indices,index]
  test_input[:,3] = test_ssta[selected_indices,index]
  test_output = np.zeros((len(selected_indices),4))
  test_output_final = np.zeros((len(selected_indices),1))

  cross_val_output = np.zeros((val_len,4))
  test_val_output = np.zeros((val_len,4))
  cb_model = CatBoostRegressor(random_seed=42,verbose=False,use_best_model=True,iterations=100)
  cb_model.fit(input,output,eval_set=(val_input,val_output))
  cross_val_output[:,0] = cb_model.predict(val_input)
  test_output[:,0] = cb_model.predict(test_input)
  rf = RandomForestRegressor(n_estimators = 100, random_state = 42)
  rf.fit(input,output)
  cross_val_output[:,1] = rf.predict(val_input)
  test_output[:,1] = rf.predict(test_input)
  lgb_model = lightgbm.LGBMRegressor(n_estimators = 100, random_state = 42,verbose= -1)
  lgb_model.fit(input,output,eval_set=(val_input,val_output))
  cross_val_output[:,2] = lgb_model.predict(val_input)
  test_output[:,2] = lgb_model.predict(test_input)
  xgb_model = xgboost.XGBRegressor(n_estimators=100,random_state=42)
  xgb_model.fit(input,output,eval_set=[(val_input,val_output)], verbose=False)#
  cross_val_output[:,3] = xgb_model.predict(val_input)
  test_output[:,3] = xgb_model.predict(test_input)

  meta_lasso = linear_model.LinearRegression(fit_intercept=False)#.Lasso(alpha=0.01,fit_intercept=False)#
  meta_lasso.fit(cross_val_output,val_output)
  test_val_output[:,0] = meta_lasso.predict(cross_val_output)
  test_output_final[:,0] = meta_lasso.predict(test_output)


  model_error1 = mean_squared_error(val_output, cross_val_output[:,0])
  model_error2 = mean_squared_error(val_output, cross_val_output[:,1])
  model_error3 = mean_squared_error(val_output, cross_val_output[:,2])
  model_error4 = mean_squared_error(val_output, cross_val_output[:,3])
  model_error = mean_squared_error(val_output, test_val_output[:,0])
  no_model_error = mean_squared_error(val_output, val_input[:,3])
  print(np.sqrt(model_error),np.sqrt(no_model_error),np.sqrt(model_error1),np.sqrt(model_error2),np.sqrt(model_error3),np.sqrt(model_error4))
  test_predictions[:,index] = test_output_final[:,0]



0


<ipython-input-10-6ee64742bfd1>:39: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  rf.fit(input,output)
/usr/local/lib/python3.10/dist-packages/sklearn/utils/validation.py:1143: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/usr/local/lib/python3.10/dist-packages/lightgbm/basic.py:300: UserWarning: Converting column-vector to 1d array
  _log_warning('Converting column-vector to 1d array')


0.08085157394159814 0.6446851733421405 0.22607094204858788 0.10562238507220524 0.15387919628808155 0.08087447490551751
1


<ipython-input-10-6ee64742bfd1>:39: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  rf.fit(input,output)
/usr/local/lib/python3.10/dist-packages/sklearn/utils/validation.py:1143: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/usr/local/lib/python3.10/dist-packages/lightgbm/basic.py:300: UserWarning: Converting column-vector to 1d array
  _log_warning('Converting column-vector to 1d array')


0.07481572510818435 0.6079909818721498 0.22949719194899648 0.09600487389660017 0.15500088655831046 0.07388329588565733
2


...

0.06323380228824951 0.47821281664655246 0.18326533180636193 0.06690882782190895 0.11737967216295592 0.06338976664605225
5772


<ipython-input-10-6ee64742bfd1>:39: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  rf.fit(input,output)
/usr/local/lib/python3.10/dist-packages/sklearn/utils/validation.py:1143: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/usr/local/lib/python3.10/dist-packages/lightgbm/basic.py:300: UserWarning: Converting column-vector to 1d array
  _log_warning('Converting column-vector to 1d array')


0.07595534534373163 0.6832472714002089 0.25835698372650806 0.10480596100240389 0.1693062971834114 0.07621349420095519
5773


<ipython-input-10-6ee64742bfd1>:39: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  rf.fit(input,output)
/usr/local/lib/python3.10/dist-packages/sklearn/utils/validation.py:1143: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/usr/local/lib/python3.10/dist-packages/lightgbm/basic.py:300: UserWarning: Converting column-vector to 1d array
  _log_warning('Converting column-vector to 1d array')


0.2170358396645335 1.1908808273974074 0.5001739295032385 0.22200581468109593 0.39908667693046235 0.23526536355484365


In [ ]:
test_predictions.shape

(71, 5774)

In [ ]:
pd.DataFrame(test_predictions).to_csv(f'{Directory}predictions.csv', index=False, header=False)

In [ ]:
from google.colab import runtime
runtime.unassign()